In [1]:
from huggingface_hub import notebook_login

notebook_login()

In [2]:

from transformers import (
    AutoTokenizer,
    DataCollatorWithPadding,
    Trainer,
    TrainingArguments,
)
from utils import ConsistentSentenceClassifier, get_metrics, load_dataset

In [3]:
tokenizer = AutoTokenizer.from_pretrained("line-corporation/line-distilbert-base-japanese")
dataset = load_dataset('train-v1.1.json')
tokenized_dataset = dataset.map(
    lambda examples: tokenizer(examples["text"], padding='max_length', truncation=True), batched=True
)

                                                  text  label
512  カーキ色の服を着た男性が、口元にリンゴを当てています。[SEP]カーキ色の服を着た男性が、口...      0
513    男性がグラウンドでボールを投げています。[SEP]白い髯を生やした男性がボールを投げています。      1
514  椅子に座った子供が、手づかみで食事をしています。[SEP]椅子に座った子供が手づかみで、食事...      2
515         プロペラ機が何台も駐機しています。[SEP]プロペラ機が何台も連なって飛んでいます。      0
516  消火栓から水が勢いよく噴き出しています。[SEP]水が噴き出している消火栓の水を浴びるように...      1
517  冷蔵庫のないキッチンにナイフとフォークが置かれています。[SEP]冷蔵庫の置かれたキッチンに...      0
518  うみでサーフィンをしているひとがいます。[SEP]黒いウェットスーツを着た人がサーフボードに...      1
519             池から白い鳥が飛び立っています。[SEP]森にある水の上を鳥が飛んでいます。      1
520       丈夫なビーチパラソルが立っています。[SEP]ビーチパラソルの支柱が折れ曲がっています。      0
521  白髪の男性が少女から花束を受け取っています。[SEP]花束を持った男性の前に多くの子供たちが...      1
                                                text  label
0    赤いひとつの傘に、二人の人が入っています。[SEP]歩道を歩く通行人が傘をさして歩いています。      1
1              川を小さなボートが進んで行きます。[SEP]川を豪華客船が進んでいきます。      0
2  ゲレンデのこぶでスキージャンプしています。[SEP]雪上でモーグルを楽しむ水色のウェアを着た女性。      1
3       黒いお皿に乗っているピザをカットしています。[SEP]黒い皿の上にピザが盛られています。      2
4    女性が目を細めて携帯電話で

Map:   0%|          | 0/19561 [00:00<?, ? examples/s]

Asking to pad to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no padding.
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Map:   0%|          | 0/512 [00:00<?, ? examples/s]

In [ ]:
model = ConsistentSentenceClassifier(
    freeze_bert=True)

training_args = TrainingArguments(
    output_dir="../factual-consistency-classification-ja-avgpool",
    learning_rate=1e-4,
    per_device_train_batch_size=64,
    per_device_eval_batch_size=8,
    num_train_epochs=30,
    weight_decay=0.02,
    evaluation_strategy="epoch",
    eval_accumulation_steps=4,
    save_strategy="epoch",
    load_best_model_at_end=True,
    save_total_limit=5,
    push_to_hub=True,
)

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=tokenized_dataset["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=get_metrics(),
)

trainer.train()
trainer.push_to_hub('factual-consistency-classification-ja-avgpool')